In [111]:
from graph import *
from models import *
from metrics import *

import pandas as pd
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import pickle as pkl

from scipy.optimize import curve_fit, approx_fprime
from multiprocess import Pool, cpu_count

In [5]:
n_cpus = cpu_count()

In [2]:
# load data from the spreadsheet which defines the structure of the workflow,
# as well as the parameters for data rates, efficiency, data reduction, and classifier performance
# ...these are taken from predictions for the Run-5 CMS
run5_system = dataframes_from_spreadsheet("cms_system_200.xlsx")
run5_smartpx_system = dataframes_from_spreadsheet("cms_system_200_smartpx.xlsx")

In [7]:
run5_system.detectors

Category          Detector  Data (bytes)  Sample Rate  Compression  \
0      Tracking     Inner Tracker       1440000     40000000            0   
1      Tracking  Outer Tracker PS        720000     40000000            0   
2      Tracking  Outer Tracker 2S        430000     40000000            0   
3      Tracking  Track Finder TPG         10000     40000000            0   
4        Timing    MIP Timing BTL        240000     40000000            0   
5        Timing    MIP Timing ETL        440000     40000000            0   
6   Calorimetry       ECAL Barrel        600000     40000000            0   
7   Calorimetry       HCAL Barrel        240000     40000000            0   
8   Calorimetry           HCAL HO         30000     40000000            0   
9   Calorimetry           HCAL HF         60000     40000000            0   
10  Calorimetry             HGCAL       3000000     40000000            0   
11  Calorimetry  HGCAL TPG Stage1        150000     40000000            0   
12  Calorimetry  HGCAL TPG Stage2         50000     40000000            0   
13         Muon           Muon DT        150000     40000000            0   
14         Muon          Muon CSC        470000     40000000            0   
15         Muon      Muon GEM GE1          3000     40000000            0   
16         Muon      Muon GEM GE2          2000     40000000            0   
17         Muon      Muon GEM ME0        120000     40000000            0   
18         Muon          Muon RPC         10000     40000000            0   

    Link Efficiency (J/bit)  Op Efficiency (J/op)  PU 200  
0              2.220000e-11                     0   1.440  
1              2.220000e-11                     0   0.720  
2              2.220000e-11                     0   0.430  
3              2.220000e-11                     0   0.010  
4              2.220000e-11                     0   0.240  
5              2.220000e-11                     0   0.440  
6              2.220000e-11                     0   0.600  
7              2.220000e-11                     0   0.240  
8              2.220000e-11                     0   0.030  
9              2.220000e-11                     0   0.060  
10             2.220000e-11                     0   3.000  
11             2.220000e-11                     0   0.150  
12             2.220000e-11                     0   0.050  
13             2.220000e-11                     0   0.150  
14             2.220000e-11                     0   0.470  
15             2.220000e-11                     0   0.003  
16             2.220000e-11                     0   0.002  
17             2.220000e-11                     0   0.120  
18             2.220000e-11                     0   0.010

In [8]:
run5_system.triggers

Name        Output  Data (bytes)  Reduction Ratio Classifier  \
0      Tracking  Intermediate             0              1.0      Dummy   
1        Timing  Intermediate             0              1.0      Dummy   
2   Calorimetry  Intermediate             0              1.0      Dummy   
3          Muon  Intermediate             0              1.0      Dummy   
4  Intermediate        Global        260000             53.3        L1T   
5        Global          Disk             0            100.0        HLT   
6          Disk           NaN             0              1.0      Dummy   

   Skill mean  Skill variance  Link Efficiency (J/bit)  Op Efficiency (J/op)  \
0           0               0             2.500000e-11                 0.000   
1           0               0             2.500000e-11                 0.000   
2           0               0             2.500000e-11                 0.000   
3           0               0             2.500000e-11                 0.000   
4           0               0             2.500000e-11                 0.003   
5           4               1             2.500000e-11                16.000   
6           0               0             2.500000e-11                 0.000   

   Compression  
0            0  
1            0  
2            0  
3            0  
4            0  
5            0  
6            0

In [9]:
#import the data predicting wall time scaling by pileup
scaling = pd.read_excel("wall time scaling.xlsx", sheet_name="Data")
#fit a polynomial to this data for CPU and GPU runtimes
fit_poly = lambda x, k3, k2, k1: k3 * x ** 3 + k2 * x ** 2 + k1 * x
k, cv = curve_fit(fit_poly, scaling["Size"], scaling["Wall Time"])
k_gpu, cv_gpu = curve_fit(fit_poly, scaling["Size"], scaling["Wall Time GPU"])

In [10]:
#define a dictionary with functions defining the scaling of trigger runtimes with incoming data
funcs = {"Global": lambda x: fit_poly(x, *k), "Intermediate": lambda x: x / 2.0e6}
funcs_gpu = {"Global": lambda x: fit_poly(x, *k_gpu), "Intermediate": lambda x: x / 2.0e6}

In [11]:
"""
Vary the accept rate of the level 1 trigger and inspect its impact on performance and resources required
"""
def init_system(system: System, functions, reduction: float):
    t = system.triggers.copy()
    #intermediate reduction stage
    t.at[4, "Reduction Ratio"] = reduction
    g = construct_graph(system.detectors, t, system.globals, functions)

    return g

In [12]:
reduction_to_ratio(0.0)

1.0

In [13]:
ex_gpu = init_system(run5_system, funcs_gpu, 53.3)

/Users/wilkie/code/system_flow/classifier.py:200: IntegrationWarning: The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probably gain from splitting up the interval and calling the integrator 
  on the subranges.  Perhaps a special-purpose integrator should be used.
  fit = lambda l: np.abs(self.egamma_rate - quad(lambda x: self.exp_dist(x, l) * interpolator(x), np.min(xs), np.max(xs))[0])
/Users/wilkie/code/system_flow/classifier.py:424: IntegrationWarning: The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probabl

In [14]:
ex_reduction = init_system(run5_smartpx_system, funcs_gpu, 53.3)

/Users/wilkie/code/system_flow/classifier.py:200: IntegrationWarning: The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probably gain from splitting up the interval and calling the integrator 
  on the subranges.  Perhaps a special-purpose integrator should be used.
  fit = lambda l: np.abs(self.egamma_rate - quad(lambda x: self.exp_dist(x, l) * interpolator(x), np.min(xs), np.max(xs))[0])
/Users/wilkie/code/system_flow/classifier.py:424: IntegrationWarning: The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probabl

In [15]:
#current l1t accept / skill
ex = init_system(run5_system, funcs, 400)

/Users/wilkie/code/system_flow/classifier.py:200: IntegrationWarning: The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probably gain from splitting up the interval and calling the integrator 
  on the subranges.  Perhaps a special-purpose integrator should be used.
  fit = lambda l: np.abs(self.egamma_rate - quad(lambda x: self.exp_dist(x, l) * interpolator(x), np.min(xs), np.max(xs))[0])
/Users/wilkie/code/system_flow/classifier.py:424: IntegrationWarning: The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probabl

In [16]:
ex.nodes["Intermediate"]["reduction ratio"]

np.float64(400.0)

In [17]:
ex.nodes["Intermediate"]["classifier"].skill_boost

0.0

In [18]:
ratio_to_reduction(ex.nodes["Intermediate"]["reduction ratio"])

np.float64(0.9975)

In [19]:
ex.graph["op power"] / 1e6

np.float64(44.51603900446542)

In [20]:
ex.nodes["Intermediate"]["output rate"]

np.int64(98669)

In [21]:
ex.nodes["Intermediate"]["input rate"] / ex.nodes["Intermediate"]["output rate"]

np.float64(405.3958183421338)

In [22]:
ex.nodes["Intermediate"]["input rate"]

np.int64(40000000)

In [23]:
ex.nodes["Global"]["input rate"] / ex.nodes["Global"]["output rate"]

np.float64(98.47205588822355)

In [24]:
ex.nodes["Global"]["output rate"]

np.int64(1002)

In [25]:
ex.nodes["Global"]["input rate"]

np.int64(98669)

In [26]:
from copy import deepcopy

In [27]:
def extract_results(graph):

    power = graph.graph["op power"] + graph.graph["link power"]
    confusion = graph.graph["performance"]

    return power, confusion

In [28]:
def vary_system(graph, reduction_ratio: float, skill: float):
    graph = deepcopy(graph)
    graph.nodes["Intermediate"]["reduction ratio"] = reduction_ratio
    graph.nodes["Intermediate"]["classifier"].skill_boost = skill

    graph = update_throughput(graph)

    power = graph.graph["op power"] + graph.graph["link power"]
    confusion = graph.graph["performance"]

    #return power, confusion, graph
    return power, confusion

In [29]:
baseline = vary_system(ex, 400, 0.0)

In [30]:
tracking_l1t = vary_system(ex, 400, 0.4)

In [31]:
gpu_system = vary_system(ex_gpu, 53.3, 0.0)
phase2_system = vary_system(ex_gpu, 53.3, 0.4)

In [32]:
smart_system = vary_system(ex_reduction, 53.3, 0.4)

In [33]:
system_labels = ["Phase-1", "L1 Tracks", "GPU", "L1 Tracks + GPU", "L1T Tracks, GPU, Smart Sensing"]

In [34]:
all_systems = [baseline, tracking_l1t, gpu_system, phase2_system, smart_system]

In [35]:
r = vary_system(ex, 100, 0.0)

In [36]:
r[0] / 1e6

np.float64(179.0151665693596)

In [37]:
#its predicted confusion matrix for the workflow
r[1]

array([[39993274,     2729],
       [    2724,     1269]])

In [38]:
#vary this accept rate from today's rate to the planned Run-5 
l1t_reductions = np.linspace(450, 40, 101)
l1t_skills = np.linspace(0, 1.0, 101)

In [39]:
pmap_args = []
for r in l1t_reductions:
    for s in l1t_skills:
        pmap_args.append((ex, r, s))

In [40]:
def map_fn(x):
    return vary_system(x[0], x[1], x[2])

In [41]:
with Pool(n_cpus) as pool:
    res = pool.map(map_fn, pmap_args)

In [43]:
with open("result.pkl", "wb") as f:
    pkl.dump(res, f)

In [44]:
# with open("result.pkl", "rb") as f:
#     res = pkl.load(f)

In [45]:
len(res)

10201

In [46]:
range(0, 101**2, 101)

range(0, 10201, 101)

In [47]:
res2 = [res[i:i+len(l1t_skills)] for i in range(0, len(l1t_skills)*len(l1t_reductions), len(l1t_skills))]

In [48]:
len(res2)

101

In [49]:
len(res2[0])

101

In [50]:
def sys_productivity(confusion, power):
    n = np.sum(get_passed(confusion))
    f1 = f1_score(confusion)
    productivity = (n * f1) / power
    return productivity

In [51]:
def extract_metrics(results):
    all_confusion = np.array([r[1] for r in results])

    all_power = [r[0] / density_scale_model(2032) for r in results]
    all_power = np.array(all_power)

    all_recall = np.array([recall(all_confusion[i,:,:]) for i in range(all_confusion.shape[0])])
    all_precision = np.array([precision(all_confusion[i,:,:]) for i in range(all_confusion.shape[0])])
    all_f1 = np.array([f1_score(all_confusion[i,:,:]) for i in range(all_confusion.shape[0])])
    all_productivity = [sys_productivity(all_confusion[i,:,:], all_power[i]) for i in range(all_confusion.shape[0])]

    metrics = {"confusion": all_confusion,
               "power": all_power,
               "recall": all_recall,
               "precision": all_precision,
               "f1 score": all_f1,
               "productivity": all_productivity,}

    return metrics

In [52]:
run5_metrics = [extract_metrics(r) for r in res2]

In [53]:
res_f1 = np.stack([r["f1 score"] for r in run5_metrics]).transpose()

In [54]:
res_recall = np.stack([r["recall"] for r in run5_metrics]).transpose()

In [55]:
res_precision = np.stack([r["precision"] for r in run5_metrics]).transpose()

In [56]:
power = np.stack([r["power"] for r in run5_metrics]).transpose()

In [57]:
res_productivity = np.stack([r["productivity"] for r in run5_metrics]).transpose()

In [58]:
from scipy.ndimage import gaussian_filter

In [59]:
smoothed_f1 = gaussian_filter(res_f1, sigma=3)

In [60]:
smoothed_productivity = gaussian_filter(res_productivity, sigma=3)

In [61]:
np.savez_compressed("smoothed_f1.npz", smoothed_f1)

In [62]:
c = ex.nodes["Intermediate"]["classifier"]

In [63]:
fig = go.Figure(data = go.Histogram(x = c.null_scores, name = "False"))
fig.add_trace(go.Histogram(x = c.pos_scores, name = "True"))
fig.update_layout(width =800, height = 600,
                  title = "Histogram of L1T Classifier Model Scores")
fig.show()

In [64]:
systems_f1 = np.array([f1_score(s[1]) for s in all_systems])

In [65]:
systems_power = np.array([s[0] / density_scale_model(2032) for s in all_systems])

In [66]:
systems_power / 1e6

array([ 6.86807398,  6.93752417, 25.8550113 , 25.84677568, 20.41667597])

In [67]:
systems_reductions = np.array([400, 400, 53.3, 53.3, 53.3])
l1t_improvement = np.array([0.0, 0.4, 0.0, 0.4, 0.4])

In [68]:
fig = go.Figure(data =
    go.Contour(
        z=smoothed_f1,
        x=l1t_reductions, # horizontal axis
        y=l1t_skills, # vertical axis,
        contours = dict(showlabels = True),
        colorbar = dict(title = "F1 Score")
         
    ),
    )

y_offset = 0.015
fig.add_trace(go.Scatter(x = systems_reductions[0:1],
                        y = l1t_improvement[0:1] + y_offset,
                        mode = "markers",
                        marker = dict(size = 14, color = "gray", symbol="circle"),
                        name = "Phase-1"))

fig.add_trace(go.Scatter(x = systems_reductions[1:2],
                        y = l1t_improvement[1:2],
                        mode = "markers",
                        marker = dict(size = 14, color = "gray", symbol = "square"),
                        name = "L1 Tracks"))

fig.add_trace(go.Scatter(x = systems_reductions[2:3],
                        y = l1t_improvement[2:3] + y_offset,
                        mode = "markers",
                        marker = dict(size = 14, color = "gray", symbol = "cross"),
                        name = "Increased L1T Accept"))

fig.add_trace(go.Scatter(x = systems_reductions[3:4],
                        y = l1t_improvement[3:4],
                        mode = "markers",
                        marker = dict(size = 14, color = "gray", symbol = "star"),
                        name = "Phase-2"))

# fig.add_trace(go.Scatter(x = systems_reductions[0:4],
#     y = l1t_improvement[0:4],
#     mode = "markers+text",
#     marker = dict(size = 14,
#             color = ["white", "blue", "red", "purple"]),
#     text =  system_labels[0:4],
#     textposition = "top left",
#     textfont = dict(color = "rgb(255, 255, 255)")       ))

fig.update_layout(width = 800, 
                  height = 600,
                  xaxis_title = "L1T Reduction Ratio",
                  yaxis_title = "L1T Skill Improvement",
                  title = "F1 Score by L1T Skill & Reduction Ratio",
                  legend=dict(xanchor = "right",
                    x = 0.95))
fig.update_xaxes(autorange="reversed")
fig.update_yaxes(range=[0.0, 0.8])
fig.show()

In [69]:
fig = go.Figure(data =
    go.Contour(
        z=smoothed_f1,
        x=l1t_reductions, # horizontal axis
        y=l1t_skills, # vertical axis,
        contours = dict(showlabels = True),
        colorbar = dict(title = "F1 Score")
         
    ),
    )

y_offset = 0.015
fig.add_trace(go.Scatter(x = systems_reductions[0:1],
                        y = l1t_improvement[0:1] + y_offset,
                        mode = "markers",
                        marker = dict(size = 14, color = "gray", symbol="circle"),
                        name = "Phase-1"))

fig.add_trace(go.Scatter(x = systems_reductions[1:2],
                        y = l1t_improvement[1:2],
                        mode = "markers",
                        marker = dict(size = 14, color = "gray", symbol = "square"),
                        name = "L1 Tracks"))

fig.add_trace(go.Scatter(x = systems_reductions[2:3],
                        y = l1t_improvement[2:3] + y_offset,
                        mode = "markers",
                        marker = dict(size = 14, color = "gray", symbol = "cross"),
                        name = "Increased L1T Accept"))

fig.add_trace(go.Scatter(x = systems_reductions[3:4],
                        y = l1t_improvement[3:4],
                        mode = "markers",
                        marker = dict(size = 14, color = "gray", symbol = "star"),
                        name = "Phase-2"))

# fig.add_trace(go.Scatter(x = systems_reductions[0:4],
#     y = l1t_improvement[0:4],
#     mode = "markers+text",
#     marker = dict(size = 14,
#             color = ["white", "blue", "red", "purple"]),
#     text =  system_labels[0:4],
#     textposition = "top left",
#     textfont = dict(color = "rgb(255, 255, 255)")       ))

fig.update_layout(width = 800, 
                  height = 600,
                  xaxis_title = "L1T Reduction Ratio",
                  yaxis_title = "L1T Skill Improvement",
                  title = "F1 Score by L1T Skill & Reduction Ratio",
                  legend=dict(xanchor = "right",
                    x = 0.95))
fig.update_xaxes(autorange="reversed")
fig.update_yaxes(range=[0.0, 0.8])
fig.show()

In [70]:
fig = go.Figure(data =
    go.Contour(
        z=smoothed_productivity * 1e3,
        x=l1t_reductions, # horizontal axis
        y=l1t_skills, # vertical axis,
        contours = dict(showlabels = True),
        colorbar = dict(title = "Productivity (1/kJ)")
         
    ),
    )

y_offset = 0.015
fig.add_trace(go.Scatter(x = systems_reductions[0:1],
                        y = l1t_improvement[0:1] + y_offset,
                        mode = "markers",
                        marker = dict(size = 14, color = "green", symbol="circle"),
                        name = "Phase-1"))

fig.add_trace(go.Scatter(x = systems_reductions[1:2],
                        y = l1t_improvement[1:2],
                        mode = "markers",
                        marker = dict(size = 14, color = "green", symbol = "square"),
                        name = "L1 Tracks"))

fig.add_trace(go.Scatter(x = systems_reductions[2:3],
                        y = l1t_improvement[2:3] + y_offset,
                        mode = "markers",
                        marker = dict(size = 14, color = "green", symbol = "cross"),
                        name = "Increased L1T Accept"))

fig.add_trace(go.Scatter(x = systems_reductions[3:4],
                        y = l1t_improvement[3:4],
                        mode = "markers",
                        marker = dict(size = 14, color = "green", symbol = "star"),
                        name = "Phase-2"))

# fig.add_trace(go.Scatter(x = systems_reductions[0:4],
#     y = l1t_improvement[0:4],
#     mode = "markers+text",
#     marker = dict(size = 14,
#             color = ["white", "blue", "red", "purple"]),
#     text =  system_labels[0:4],
#     textposition = "top left",
#     textfont = dict(color = "rgb(255, 255, 255)")       ))

fig.update_layout(width = 800, 
                  height = 600,
                  xaxis_title = "L1T Reduction Ratio",
                  yaxis_title = "L1T Skill Improvement",
                  title = "Productivity by L1T Skill & Reduction Ratio",
                  legend=dict(xanchor = "right",
                    x = 0.95))
fig.update_xaxes(autorange="reversed")
fig.update_yaxes(range=[0.0, 0.8])
fig.add_annotation(x = -0.1, 
                   y = -0.1, 
                   showarrow=False,
                   text = "Pileup = 200", 
                   xref="paper", 
                   yref="paper",
                   font = dict(size = 14))
fig.show()

In [71]:
fig = go.Figure(data =
    go.Contour(
        z=power,
        x=l1t_reductions, # horizontal axis
        y=l1t_skills, # vertical axis,
         contours_coloring='heatmap',
    ),
    )
fig.update_layout(width = 800, 
                  height = 600,
                  title = "Power by Trigger Skill & Reduction Ratio",
                  xaxis=dict(
                        title="Reduction Ratio",
                        titlefont=dict(size=24, family='Arial, bold')  # Bold font for the x-axis title
                    ),
                    yaxis=dict(
                        title="Skill",
                        titlefont=dict(size=24, family='Arial, bold')  # Bold font for the y-axis title
                    ),
                    font = dict(size=18,),)
fig.update_xaxes(autorange="reversed")
fig.show()

In [72]:
#because its rejection is so much higher, there's more potential improvement gained by making L1T's skill higher 
#than simply passing more data to the HLT

In [73]:
fig = go.Figure(data =
    go.Contour(
        z = smoothed_f1,
        x=power[0,:], # horizontal axis
        y=l1t_skills, # vertical axis,
         contours_coloring='heatmap',
         contours = dict(showlabels = True)
    ),
    )
fig.update_layout(width = 800,
                  height = 600,
                  title = "F1 Score by Skill Improvement and Power",
                  xaxis_title = "Power",
                  yaxis_title = "L1T Skill Improvement")
fig.update_yaxes(range=(0.0, 0.8))
fig.show()

In [74]:
fig = go.Figure(data =
    go.Contour(
        z = np.transpose(smoothed_f1),
        y=power[0,:], # horizontal axis
        x=l1t_skills, # vertical axis,
         contours_coloring='heatmap',
         contours = dict(showlabels = True)
    ),
    )

fig.add_trace(go.Scatter(y = systems_power[0:1],
                        x = l1t_improvement[0:1],
                        mode = "markers",
                        marker = dict(size = 14, color = "gray"),
                        name = "Phase-1"))

fig.add_trace(go.Scatter(y = systems_power[1:2],
                        x = l1t_improvement[1:2],
                        mode = "markers",
                        marker = dict(size = 14, color = "red"),
                        name = "L1T Tracking"))

fig.add_trace(go.Scatter(y = systems_power[2:3],
                        x = l1t_improvement[2:3],
                        mode = "markers",
                        marker = dict(size = 14, color = "blue"),
                        name = "Increased L1T Accept"))

fig.add_trace(go.Scatter(y = systems_power[3:4],
                        x = l1t_improvement[3:4],
                        mode = "markers",
                        marker = dict(size = 14, color = "purple"),
                        name = "Phase-2"))

fig.add_trace(go.Scatter(y = systems_power[4:],
                        x = l1t_improvement[4:],
                        mode = "markers",
                        marker = dict(size = 14, color = "green"),
                        name = "Data Reduction"))

fig.update_layout(width = 800,
                  height = 600,
                  title = "F1 Score by Skill Improvement and Power",
                  yaxis_title = "Power",
                  xaxis_title = "L1T Skill Improvement",
                  legend=dict(xanchor = "right",
                    x = 0.95))
fig.update_xaxes(range=(0.0, 0.7))
fig.show()

In [75]:
output_rate = np.array([1e3, 1e3, 7.5e3, 7.5e3, 7.5e3])

In [76]:
output_rate

array([1000., 1000., 7500., 7500., 7500.])

In [ ]:
f1_score()

In [95]:
ex_reduction["Global"]

AtlasView({'Disk': {'link efficiency': np.float64(2.5e-11), 'statistics': array([4586, 2922]), 'message size': np.float64(7647400.0), 'throughput': np.float64(57416679200.0), 'energy': np.float64(0.0015294800000000002), 'power': np.float64(11.48333584)}})

In [77]:
productivity = (systems_f1 * output_rate) / systems_power

In [78]:
systems_f1

array([0.219     , 0.39139139, 0.38970392, 0.88537256, 0.79492826])

In [79]:
productivity

array([3.18866688e-05, 5.64165806e-05, 1.13044987e-04, 2.56909963e-04,
       2.92014330e-04])

In [80]:
fig = go.Figure(data =
    go.Bar(
        x = ["Phase-1", "L1T Tracking", "Increased L1T Accept", "Phase-2", "Data Reduction"],
        y= productivity
    ),
    )



fig.update_layout(width = 800,
                  height = 600,
                  title = "Productivity by System",
                  yaxis_title = "Productivity (Relevant Samples per Joule)",
                  xaxis_title = "System", )

fig.show()

In [84]:
ex_reduction.nodes["Inner Tracker"]["message size"]

np.int64(662400)

In [93]:
ex_reduction.nodes["Intermediate"]["op efficiency"]

np.float64(0.003)

In [89]:
ex_reduction.nodes["Global"]["classifier"].skill_boost

0.0

In [94]:
#final system model - tracker l1t upgrade w/ smart pixels

c0 = [ex_reduction.nodes["Inner Tracker"]["message size"],
      ex_reduction.nodes["HGCAL"]["message size"],
      53.3, #reduction ratio
      0.4, #l1t skill boost
      0.0, #hlt skill boost
      ex_reduction.nodes["Intermediate"]["op efficiency"],
      ex_reduction.nodes["Global"]["op efficiency"],]


In [112]:
c0

[np.int64(662400),
 np.int64(3000000),
 53.3,
 0.4,
 0.0,
 np.float64(0.003),
 np.float64(16.0)]

In [126]:
def vary_parameters(graph, tracker_data, hgcal_data, reduction_ratio, l1t_skill, hlt_skill, l1t_eff, hlt_eff):
    graph = deepcopy(graph)
    #system parameters
    graph.nodes["Inner Tracker"]["sample data"] = tracker_data
    graph.nodes["HGCAL"]["sample data"] = hgcal_data
    graph.nodes["Intermediate"]["reduction ratio"] = reduction_ratio

    #algorithm parameters
    graph.nodes["Intermediate"]["classifier"].skill_boost = l1t_skill
    graph.nodes["Global"]["classifier"].skill_boost = hlt_skill

    #tech parameters
    graph.nodes["Intermediate"]["op efficiency"] = l1t_eff
    graph.nodes["Global"]["op efficiency"] = hlt_eff

    #update the graph
    graph = update_throughput(graph)

    #calc productivity
    power = (graph.graph["op power"] + graph.graph["link power"]) / density_scale_model(2032)
    confusion = graph.graph["performance"]
    prod = (f1_score(confusion) * 7500) / power
    return prod
    

In [131]:
vary_parameters(ex_reduction, *c0)

np.float64(0.0002920143304319754)

In [133]:
vp = lambda x: vary_parameters(ex_reduction, *x)

In [134]:
c0a = np.array(c0)

In [140]:
approx_fprime(c0a,
                vp,
                [1e2,
                 1e2,
                 1, 
                 0.05,
                 0.05,
                 1e-4,
                 1e-1],
              )

array([-9.15160376e-11, -9.15160376e-11,  5.07211514e-06,  1.91989012e-05,
        5.31427565e-06, -3.36533426e-04, -1.80598950e-05])